In [1]:
import sys, os
from bs4 import BeautifulSoup
import requests
from selenium import webdriver
import selenium
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from webdriver_manager.chrome import ChromeDriverManager
from datetime import datetime, timedelta
from pandas import DataFrame
import time
from openpyxl.workbook import Workbook

sleep_sec = 0.5

wb = Workbook()

# User-Agent를 입력해주세요!
headers = {'User-Agent' : '________________'}

query = '데이터'
yesterday = (datetime.today() - timedelta(1)).strftime("%Y.%m.%d")

def news_crawling():
    
    service = Service(executable_path=ChromeDriverManager().install())
    browser = webdriver.Chrome(service=service)


    print('브라우저를 실행시킵니다(자동 제어)\n')

    news_url = 'https://search.naver.com/search.naver?where=news&query={0}&sm=tab_opt&sort=0&photo=0&field=0&pd=3&ds={1}&de={1}]'.format(query, yesterday)
    browser.get(news_url)
    time.sleep(sleep_sec)
    

    print('\n크롤링을 시작합니다.')

    #####동적 제어로 페이지 넘어가며 크롤링
    news_dict = {}
    idx = 1
    cur_page = 1
    news_num = 1000000

    while True:

        table = browser.find_element_by_xpath('//ul[@class="list_news"]')
        li_list = table.find_elements_by_xpath('./li[contains(@id, "sp_nws")]')
        area_list = [li.find_element_by_xpath('.//div[@class="news_wrap api_ani_send"]') for li in li_list]
                
        for a in area_list[:min(len(area_list), news_num-idx+1)]:
            n = a.find_element_by_xpath('.//a[@class="news_tit"]')
            n_url = n.get_attribute('href')
                    
            try:
                img = a.find_element(By.CSS_SELECTOR,'a.dsc_thumb ').find_element(By.CSS_SELECTOR, 'img')
                img = img.get_attribute('src')
                
            except:
                img = " "
                    
            news_dict[idx] = {'Title' : n.get_attribute('title'),
                            'url' : n_url,
                            'thumbnail': img}
            
            idx += 1
            
            
        try:
            next_btn = browser.find_element(By.CSS_SELECTOR, 'a.btn_next')
            next_btn.click()
        
            cur_page +=1

            pages = browser.find_element_by_xpath('//div[@class="sc_page_inner"]')
            next_page_url = [p for p in pages.find_elements_by_xpath('.//a') if p.text == str(cur_page)][0].get_attribute('href')

            browser.get(next_page_url)
            time.sleep(sleep_sec)
            
        except:
            print('\n브라우저를 종료합니다.\n' + '=' * 100)
            time.sleep(0.7)
            browser.close()
            break
        
    print('데이터프레임 변환\n')
    news_df = DataFrame(news_dict).T

    folder_path = os.getcwd()
    xlsx_file_name = '{}_{}.xlsx'.format(query, yesterday)

    news_df.to_excel(xlsx_file_name, index=False)

    print('엑셀 저장 완료 | 경로 : {}\\{}\n'.format(folder_path, xlsx_file_name))
    
news_crawling()



====== WebDriver manager ======
Current google-chrome version is 101.0.4951
Get LATEST chromedriver version for 101.0.4951 google-chrome
Trying to download new driver from https://chromedriver.storage.googleapis.com/101.0.4951.41/chromedriver_mac64.zip
Driver has been saved in cache [/Users/ys/.wdm/drivers/chromedriver/mac64/101.0.4951.41]


브라우저를 실행시킵니다(자동 제어)


크롤링을 시작합니다.


/var/folders/z6/3rb_406j31vc41v5hs3kz5n80000gn/T/ipykernel_2401/3360241135.py:48: DeprecationWarning: find_element_by_xpath is deprecated. Please use find_element(by=By.XPATH, value=xpath) instead
  table = browser.find_element_by_xpath('//ul[@class="list_news"]')
/var/folders/z6/3rb_406j31vc41v5hs3kz5n80000gn/T/ipykernel_2401/3360241135.py:49: DeprecationWarning: find_elements_by_xpath is deprecated. Please use find_elements(by=By.XPATH, value=xpath) instead
  li_list = table.find_elements_by_xpath('./li[contains(@id, "sp_nws")]')
/var/folders/z6/3rb_406j31vc41v5hs3kz5n80000gn/T/ipykernel_2401/3360241135.py:50: DeprecationWarning: find_element_by_xpath is deprecated. Please use find_element(by=By.XPATH, value=xpath) instead
  area_list = [li.find_element_by_xpath('.//div[@class="news_wrap api_ani_send"]') for li in li_list]
/var/folders/z6/3rb_406j31vc41v5hs3kz5n80000gn/T/ipykernel_2401/3360241135.py:53: DeprecationWarning: find_element_by_xpath is deprecated. Please use find_element(


브라우저를 종료합니다.
데이터프레임 변환

엑셀 저장 완료 | 경로 : /Users/ys/DA_JuniorProject\데이터_2022.05.23.xlsx



In [2]:
import pandas as pd
fileName = '{}_{}.xlsx'.format(query, yesterday)
news_df = pd.read_excel(fileName, engine = "openpyxl") 

print(news_df)

                                               Title  \
0                건보공단, 연세의료원과 맞손…‘건강보험 빅데이터 분석센터’ 개소   
1                LGU+ "친환경 데이터센터로 소나무 289만 그루 심은 효과"   
2                        롯데글로벌로지스, 인하대와 물류데이터 전문가 육성   
3                      화웨이, 아태 최초 풀 스택 데이터 센터 솔루션 공개   
4                         더존비즈온, 마이데이터 종합기반 서비스 개발한다   
...                                              ...   
2507          캐시리스 시대 ‘신용카드’ 결제도 모바일로…"각사, 앱 유치 총력전"   
2508           뉴욕증시 비트코인 휘청 암호화폐 뱅크런 "인출 러시" 백악관 보고서   
2509         스웨덴 노스볼트, 유럽 기업 중 최초 배터리 생산…아시아 지배력에 도전   
2510  [교육시론] '사람이 귀한 시대' 입시의 본령을 회복해야-정석오 한국외대 입학처장    
2511            [그레이트 컴퍼니] 네이버, 양성평등·지배구조 '우수' 기업 선정   

                                                    url  \
0           https://zdnet.co.kr/view/?no=20220523111901   
1                https://www.news1.kr/articles/?4688377   
2     http://www.newsis.com/view/?id=NISX20220523_00...   
3     http://www.segye.com/content/html/2022/05/23/2...   
4         http://www.fnnews.com/

In [5]:
from konlpy.tag import Komoran
import re
from tqdm import tqdm

def process(df):
    komoran = Komoran()
    stopwords = ['을', '를', '이', '가', '은', '는']
    tokenLi = []
    for txt in tqdm(df['Title']):
        text = re.sub('[^가-힣a-z]', ' ', txt.lower())
        token = komoran.morphs(text)
        tokenLi.append([t for t in token if t not in stopwords or type(t) != float])
    return tokenLi, komoran

news_df['token'], komoran = process(news_df)

100%|█████████████████████████████████████| 2512/2512 [00:01<00:00, 2297.69it/s]


In [6]:
news_df

Title  \
0                건보공단, 연세의료원과 맞손…‘건강보험 빅데이터 분석센터’ 개소   
1                LGU+ "친환경 데이터센터로 소나무 289만 그루 심은 효과"   
2                        롯데글로벌로지스, 인하대와 물류데이터 전문가 육성   
3                      화웨이, 아태 최초 풀 스택 데이터 센터 솔루션 공개   
4                         더존비즈온, 마이데이터 종합기반 서비스 개발한다   
...                                              ...   
2507          캐시리스 시대 ‘신용카드’ 결제도 모바일로…"각사, 앱 유치 총력전"   
2508           뉴욕증시 비트코인 휘청 암호화폐 뱅크런 "인출 러시" 백악관 보고서   
2509         스웨덴 노스볼트, 유럽 기업 중 최초 배터리 생산…아시아 지배력에 도전   
2510  [교육시론] '사람이 귀한 시대' 입시의 본령을 회복해야-정석오 한국외대 입학처장    
2511            [그레이트 컴퍼니] 네이버, 양성평등·지배구조 '우수' 기업 선정   

                                                    url  \
0           https://zdnet.co.kr/view/?no=20220523111901   
1                https://www.news1.kr/articles/?4688377   
2     http://www.newsis.com/view/?id=NISX20220523_00...   
3     http://www.segye.com/content/html/2022/05/23/2...   
4         http://www.fnnews.com/news/202205231524205652   
...                                                 ...   
2507  http://www.smartfn.co.kr/view.php?ud=202205231...   
2508  http://www.g-enews.com/ko-kr/news/article/news...   
2509  http://www.g-enews.com/ko-kr/news/article/news...   
2510  http://www.veritas-a.com/news/articleView.html...   
2511  https://www.ceoscoredaily.com/page/view/202205...   

                                              thumbnail  \
0     https://search.pstatic.net/common/?src=https%3...   
1     https://search.pstatic.net/common/?src=https%3...   
2     https://search.pstatic.net/common/?src=https%3...   
3     https://search.pstatic.net/common/?src=https%3...   
4     https://search.pstatic.net/common/?src=https%3...   
...                                                 ...   
2507  https://search.pstatic.net/common/?src=https%3...   
2508  https://search.pstatic.net/common/?src=https%3...   
2509  https://search.pstatic.net/common/?src=https%3...   
2510  https://search.pstatic.net/common/?src=https%3...   
2511  https://search.pstatic.net/common/?src=https%3...   

                                                  token  
0     [건, 보, 공단, 연세, 의료원, 과, 맞, 소, ㄴ, 건강보험, 빅, 데이터, ...  
1          [lgu, 친환경, 데이터, 센터, 로, 소나무, 만, 그루, 심, 은, 효과]  
2                  [롯데글로벌로지스, 인하대, 와, 물류, 데이터, 전문가, 육성]  
3             [화웨이, 아태, 최초, 풀, ㄹ, 스택, 데이터, 센터, 솔루션, 공개]  
4        [더, 존, 비즈, 온, 마이, 데이터, 종합, 기반, 서비스, 개발, 하, ㄴ다]  
...                                                 ...  
2507  [캐시, 리스, 시대, 신용카드, 결제, 도, 모바일, 로, 각사, 앱, 유치, 총력전]  
2508    [뉴욕, 증시, 비트코인, 휘청, 암호화폐, 뱅크런, 인출, 러시, 백악관, 보고서]  
2509  [스웨덴, 노스, 볼트, 유럽, 기업, 중, 최초, 배터리, 생산, 아시아, 지배력...  
2510  [교육, 시론, 사람, 이, 귀하, ㄴ, 시대, 입시, 의, 본령, 을, 회복, 하...  
2511         [그레이트, 컴퍼니, 네이버, 양성평등, 지배, 구조, 우수, 기업, 선정]  

[2512 rows x 4 columns]

In [78]:
#nouns분석 평가, 근데 영어는?
test_df = pd.read_excel('데이터_2022.05.18.xlsx', engine = "openpyxl") 

np.random.seed(520)
numLi = np.random.randint(2510, size=20)
for i in numLi: 
    txt = test_df['Title'][i]
    text = re.sub('[^가-힣a-z]', ' ', txt.lower())
    token = komoran.nouns(text)
    print(token)
    
# for txt in tqdm(df['Title']):
#         text = re.sub('[^가-힣a-z]', ' ', txt.lower())
#         token = komoran.morphs(text)
#         tokenLi.append([t for t in token if t not in stopwords or type(t) != float])

['캐롯', '국민', '안전', '운전', '리', '워드', '서비스', '캐롯', '버스', '오토']
['추억', '기능', '실속', '제로', '싸이월드', '숙제']
['일렉트릭', '자산운용', '사와', '재생', '에너지', '공략']
['마이크로소프트', '가지', '니지', '드', '서비스', '공개', '기존', '산업', '솔루션', '서비스', '확장']
['구매', '유도', '개인화', '레시', '피']
['분당제생병원', '차세대', '병원정보시스템', '구축']
['클라우드', '시장', '승자', '독식', '전사', '양병']
['실리콘밸리', '랜드마크', '구글', '오피스', '거북', '등', '껍질']
['시론', '제조', '경쟁력', '데이터', '전략', '게임', '체인']
['디지털', '마케팅', '기업', '자동화', '리포팅', '시스템', '구축']
['저녁', '브리핑', '테라', '붕괴', '역풍']
['정부', '원전', '확대', '시장', '원칙', '전력', '시장', '구축', '추진']
['신한', '베트남', '은행', '디지털', '사업', '전담', '퓨처', '뱅크', '그룹', '출범']
['반도', '건설', '여주', '공장', '가동', '생산']
['트위터', '활성', '계정', '가짜', '인수', '보류']
['모티브', '보안', '관리', '우수', '국방부', '장관', '표창']
['학년', '대입', '전략', '지난해', '경찰대', '경쟁', '대', '국어', '수학', '영어', '탐구', '비중', '편']
['뮤직뱅크', '제작진', '임영웅', '위', '입']
['모라', '이', '파블로', '항공', '미래', '항공', '물류', '시스템', '구축', '업무', '협약', '체결']
['김지원', '손', '석', '해방', '추앙', '수', '드라마']


In [80]:
def process(df):
    komoran = Komoran()
    stopwords = ['을', '를', '이', '가', '은', '는']
    tokenLi = []
    for txt in tqdm(df['Title']):
        text = re.sub('[^가-힣a-z]', ' ', txt.lower())
        token = komoran.nouns(text)
        tokenLi.append([t for t in token if t not in stopwords or type(t) != float])
    return tokenLi, komoran

test_df['token'], komoran = process(test_df)

100%|██████████████████████████████████████| 2621/2621 [00:05<00:00, 457.09it/s]


In [83]:
test_df_loc = test_df.loc[numLi, :]

In [84]:
test_df_loc

Title  \
411                   캐롯, 전국민 안전운전 리워드서비스 '캐롯멤버스 오토' 론칭   
1263                 "추억도 기능도 그대로"…'실속 제로' 싸이월드에 남겨진 숙제   
527                            LS일렉트릭, 자산운용사와 신재생에너지 공략   
2386    마이크로소프트, 새로운 3가지 매니지드 서비스 공개 및 기존 산업 솔루션 서비스 확장   
2201                                  구매를 유도하는 초개인화 레시피   
2049                      이지케어텍, 분당제생병원에 차세대 병원정보시스템 구축   
1459                     "클라우드 시장, 승자독식"…IT전사 '40만 양병론'   
1372               “실리콘밸리의 새 랜드마크”…구글 새 오피스, 거북 등껍질 닮았네   
218                      [ET시론]제조 경쟁력, 데이터 전략이 '게임 체인저'   
2312    디지털마케팅 기업 Driven, 자동화 리포팅 시스템 'Drag In'(드래그) 구축   
2359                     [저녁브리핑] 테라 붕괴로 역풍 맞은 P2E는 어딜까?   
1828                      "새정부, 원전확대·시장원칙 전력시장 구축 추진해야"   
419                    신한베트남은행, 디지털 사업 전담 '퓨처 뱅크 그룹' 출범   
928                            반도건설, 여주 공장 가동…PC 생산 본격화   
1663                   트위터 활성 계정 20%는 가짜?...머스크 "인수 보류"   
347                           SNT모티브, 보안관리 우수…국방부 장관 표창   
2404  [2023학년도 대입 전략] 지난해 경찰대 경쟁률 92.4 대 1까지 치솟아…국어·...   
1117                          뮤직뱅크 제작진 "임영웅 2위는"...입 열다   
1890             모라이-파블로항공, 미래 항공 물류 시스템 구축 위한 업무 협약 체결   
818                   김지원X손석구 '나의 해방일지', 추앙할 수밖에 없는 드라마   

                                                    url  \
411   http://news.mk.co.kr/newsRead.php?no=439835&ye...   
1263  https://www.asiatime.co.kr/article/20220518500205   
527   http://www.dt.co.kr/contents.html?article_no=2...   
2386               https://www.ciokorea.com/news/236934   
2201                  https://platum.kr/archives/186060   
2049  http://www.m-i.kr/news/articleView.html?idxno=...   
1459  http://news.mt.co.kr/mtview.php?no=20220517154...   
1372  https://www.chosun.com/economy/tech_it/2022/05...   
218                http://www.etnews.com/20220518000043   
2312  https://www.dailysecu.com/news/articleView.htm...   
2359  http://www.coindeskkorea.com/news/articleView....   
1828  http://www.energydaily.co.kr/news/articleView....   
419   https://www.hankyung.com/economy/article/20220...   
928   http://www.constimes.co.kr/news/articleView.ht...   
1663  http://www.thedailypost.kr/news/articleView.ht...   
347   http://www.newsis.com/view/?id=NISX20220518_00...   
2404  https://www.hankyung.com/news/article/20220513...   
1117  http://www.thedrive.co.kr/news/newsview.php?nc...   
1890  https://www.job-post.co.kr/news/articleView.ht...   
818   http://starin.edaily.co.kr/news/newspath.asp?n...   

                                              thumbnail  \
411   https://search.pstatic.net/common/?src=https%3...   
1263  https://search.pstatic.net/common/?src=https%3...   
527   https://search.pstatic.net/common/?src=https%3...   
2386                                                      
2201  https://search.pstatic.net/common/?src=https%3...   
2049  https://search.pstatic.net/common/?src=https%3...   
1459  https://search.pstatic.net/common/?src=https%3...   
1372  https://search.pstatic.net/common/?src=https%3...   
218   https://search.pstatic.net/common/?src=https%3...   
2312  https://search.pstatic.net/common/?src=https%3...   
2359  https://search.pstatic.net/common/?src=https%3...   
1828  https://search.pstatic.net/common/?src=https%3...   
419   https://search.pstatic.net/common/?src=https%3...   
928   https://search.pstatic.net/common/?src=https%3...   
1663  https://search.pstatic.net/common/?src=https%3...   
347   https://search.pstatic.net/common/?src=https%3...   
2404  https://search.pstatic.net/common/?src=https%3...   
1117  https://search.pstatic.net/common/?src=https%3...   
1890  https://search.pstatic.net/common/?src=https%3...   
818   https://search.pstatic.net/common/?src=https%3...   

                                                  token  
411            [캐롯, 국민, 안전, 운전, 리, 워드, 서비스, 캐롯, 버스, 오토]  
1263                         [추억, 기능, 실속, 제로, 싸이월드, 숙제]  
527                       [일렉트릭, 자산운용, 사와, 재생, 에너지, 공략]  
2386  [마이크로소프트, 가지, 니지, 드, 서비스, 공개, 기존, 산업, 솔루션, 서비스...  
2201                               [구매, 

In [ ]:
#TF-IDF Vectorization

In [7]:
# sklearn
from sklearn.cluster import KMeans
from sklearn.manifold import TSNE
# 시각화
import seaborn as sns
import matplotlib.pyplot as plt

In [8]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.cluster import DBSCAN
import numpy as np

# 문서를 명사 집합으로 보고 문서 리스트로 치환 (tfidfVectorizer 인풋 형태를 맞추기 위해)
text = [" ".join(noun) for noun in news_df['token']]

tfidf_vectorizer = TfidfVectorizer(min_df = 5, ngram_range=(1,5))
tfidf_vectorizer.fit(text)
vector = tfidf_vectorizer.transform(text).toarray()


vector = np.array(vector) # Normalizer를 이용해 변환된 벡터
model = DBSCAN(eps=0.3,min_samples=6, metric = "cosine")
# 거리 계산 식으로는 Cosine distance를 이용
result = model.fit_predict(vector)

news_df['result'] = result
news_df

Title  \
0                건보공단, 연세의료원과 맞손…‘건강보험 빅데이터 분석센터’ 개소   
1                LGU+ "친환경 데이터센터로 소나무 289만 그루 심은 효과"   
2                        롯데글로벌로지스, 인하대와 물류데이터 전문가 육성   
3                      화웨이, 아태 최초 풀 스택 데이터 센터 솔루션 공개   
4                         더존비즈온, 마이데이터 종합기반 서비스 개발한다   
...                                              ...   
2507          캐시리스 시대 ‘신용카드’ 결제도 모바일로…"각사, 앱 유치 총력전"   
2508           뉴욕증시 비트코인 휘청 암호화폐 뱅크런 "인출 러시" 백악관 보고서   
2509         스웨덴 노스볼트, 유럽 기업 중 최초 배터리 생산…아시아 지배력에 도전   
2510  [교육시론] '사람이 귀한 시대' 입시의 본령을 회복해야-정석오 한국외대 입학처장    
2511            [그레이트 컴퍼니] 네이버, 양성평등·지배구조 '우수' 기업 선정   

                                                    url  \
0           https://zdnet.co.kr/view/?no=20220523111901   
1                https://www.news1.kr/articles/?4688377   
2     http://www.newsis.com/view/?id=NISX20220523_00...   
3     http://www.segye.com/content/html/2022/05/23/2...   
4         http://www.fnnews.com/news/202205231524205652   
...                                                 ...   
2507  http://www.smartfn.co.kr/view.php?ud=202205231...   
2508  http://www.g-enews.com/ko-kr/news/article/news...   
2509  http://www.g-enews.com/ko-kr/news/article/news...   
2510  http://www.veritas-a.com/news/articleView.html...   
2511  https://www.ceoscoredaily.com/page/view/202205...   

                                              thumbnail  \
0     https://search.pstatic.net/common/?src=https%3...   
1     https://search.pstatic.net/common/?src=https%3...   
2     https://search.pstatic.net/common/?src=https%3...   
3     https://search.pstatic.net/common/?src=https%3...   
4     https://search.pstatic.net/common/?src=https%3...   
...                                                 ...   
2507  https://search.pstatic.net/common/?src=https%3...   
2508  https://search.pstatic.net/common/?src=https%3...   
2509  https://search.pstatic.net/common/?src=https%3...   
2510  https://search.pstatic.net/common/?src=https%3...   
2511  https://search.pstatic.net/common/?src=https%3...   

                                                  token  result  
0     [건, 보, 공단, 연세, 의료원, 과, 맞, 소, ㄴ, 건강보험, 빅, 데이터, ...       0  
1          [lgu, 친환경, 데이터, 센터, 로, 소나무, 만, 그루, 심, 은, 효과]      -1  
2                  [롯데글로벌로지스, 인하대, 와, 물류, 데이터, 전문가, 육성]       1  
3             [화웨이, 아태, 최초, 풀, ㄹ, 스택, 데이터, 센터, 솔루션, 공개]       2  
4        [더, 존, 비즈, 온, 마이, 데이터, 종합, 기반, 서비스, 개발, 하, ㄴ다]      -1  
...                                                 ...     ...  
2507  [캐시, 리스, 시대, 신용카드, 결제, 도, 모바일, 로, 각사, 앱, 유치, 총력전]      -1  
2508    [뉴욕, 증시, 비트코인, 휘청, 암호화폐, 뱅크런, 인출, 러시, 백악관, 보고서]      -1  
2509  [스웨덴, 노스, 볼트, 유럽, 기업, 중, 최초, 배터리, 생산, 아시아, 지배력...      -1  
2510  [교육, 시론, 사람, 이, 귀하, ㄴ, 시대, 입시, 의, 본령, 을, 회복, 하...      -1  
2511         [그레이트, 컴퍼니, 네이버, 양성평등, 지배, 구조, 우수, 기업, 선정]      -1  

[2512 rows x 5 columns]

In [9]:
for cluster_num in set(result):
    # -1,0은 노이즈 판별이 났거나 클러스터링이 안된 경우
    if(cluster_num == -1 or cluster_num == 0): 
        continue
    else:
        print("cluster num : {}".format(cluster_num))
        temp_df = news_df[news_df['result'] == cluster_num] # cluster num 별로 조회
        for title in temp_df['Title']:
            print(title) # 제목으로 살펴보자
        print()

cluster num : 1
롯데글로벌로지스, 인하대와 물류데이터 전문가 육성
롯데글로벌로지스, 인하대 물류대학원과 '물류데이터 전문가 육성' 맞손
롯데글로벌로지스-인하대, 물류 데이터 전문가 육성 '맞손'
롯데글로벌로지스, 인하대 물류대학원과 '물류데이터 전문가 육성' 맞손
롯데글로벌로지스, 인하대 물류대학원과 '물류데이터 전문가 육성' 맞손
롯데글로벌로지스, 인하대 물류대학원과 '물류데이터 전문가' 육성
롯데글로벌로지스, 인하대 물류대학원과 ‘데이터 전문가 육성’ 맞손
롯데글로벌로지스, 인하대와 '물류데이터 전문가' 육성
롯데글로벌로지스, 인하대와 물류 데이터 전문가 육성

cluster num : 2
화웨이, 아태 최초 풀 스택 데이터 센터 솔루션 공개
화웨이, 아태지역 최초 풀 스택 데이터 센터 솔루션 공개
화웨이, 풀 스택 데이터 센터 솔루션 첫 공개
화웨이, 아태지역 최초 풀 스택 데이터 센터 솔루션 공개
화웨이, 아태지역 최초 '풀 스택 데이터 센터 솔루션' 공개
화웨이, 아태지역 첫번째 풀 스택 데이터 센터 솔루션 공개
화웨이, 아태지역 첫번째 풀 스택 데이터 센터 솔루션 공개

cluster num : 3
AI와 빅데이터로 광어양식 집단폐사 막는다
제주서 인공지능·빅데이터로 광어 양식 집단폐사 막는다
AI·빅데이터로 광어 양식 집단폐사 막는다
AI·빅데이터로 광어 집단폐사 해결
제주 광어 집단폐사 AI.빅데이터 기술로 진단
제주도, 인공지능으로 광어 집단 폐사 막는다

cluster num : 4
월 195만원, ‘공공데이터 기업매칭 청년인턴십’ 2500명 모집
'공공데이터 기업매칭 청년인턴십' 2천500명 모집
NIA, 공공데이터 기업매칭 청년인턴십 2500명 모집
NIA, 공공데이터 기업매칭 청년인턴십 2500명 모집
한국지능정보사회진흥원, ‘공공데이터 기업매칭 청년인턴십’ 2,500명 모집
NIA, '공공데이터 기업매칭 청년인턴십' 참가자 모집 개시
NIA, ‘공공데이터 기업매칭 청년인턴십’ 2500명 모집

cluster num : 5


In [ ]:
#word embedding
#pre-trained w2v

In [10]:
!pip install gensim

In [11]:
import gensim

word2vec = gensim.models.KeyedVectors.load_word2vec_format('GoogleNews-vectors-negative300.bin.gz', binary = True)

In [27]:
tmp = word2vec[news_df['token'][0][5]]
tmp.shape

(300,)

In [38]:
result_pretrained = []
for text in tqdm(news_df['token']):
    vecLi = np.zeros(300)
    for i in range(len(text)):
        try:
            wordVec = word2vec[text[i]]
        except:
            wordVec = np.zeros(300)
        vecLi = np.vstack([vecLi, wordVec])
        #vecLi.append(wordVec)
    #vecLi = np.append(vecLi, np.array([]), axis=0)
    result_pretrained.append(vecLi.mean(axis=0))
result_pretrained

100%|█████████████████████████████████████| 2512/2512 [00:00<00:00, 3631.91it/s]


[array([-2.61306763e-03, -1.39465332e-02,  5.55419922e-03,  2.28881836e-04,
        -2.36511230e-03,  6.48498535e-04,  2.65312195e-03, -3.00025940e-03,
        -2.86483765e-03,  1.62658691e-02, -8.03375244e-03,  7.61413574e-03,
        -4.31823730e-03,  1.01699829e-02,  4.38690186e-03, -1.85012817e-03,
         4.65393066e-03,  2.91252136e-03, -8.14819336e-03, -4.03976440e-03,
         3.38077545e-04, -8.17871094e-03,  2.13012695e-02,  6.92749023e-03,
        -1.19934082e-02, -1.40686035e-02,  8.56781006e-03,  5.62667847e-03,
        -4.75311279e-03, -7.30514526e-03, -8.05664062e-03, -5.28144836e-03,
         3.63159180e-03, -4.65011597e-03, -7.94219971e-03, -1.18408203e-02,
        -3.20577621e-03,  2.71224976e-03, -6.02722168e-03,  4.51850891e-03,
        -9.14001465e-03, -7.20977783e-03, -4.95624542e-03,  9.33837891e-03,
        -2.07519531e-03, -1.42822266e-02, -1.19476318e-02, -1.58691406e-02,
        -3.16238403e-03,  7.27844238e-03, -2.97851562e-02,  2.20947266e-02,
         1.2

In [40]:
news_df['result_pretrained'] = result_pretrained

In [49]:
news_df['result_pretrained']

0       [-0.002613067626953125, -0.013946533203125, 0....
1       [-0.007303873697916667, -0.026529947916666668,...
2       [-0.005279541015625, -0.00970458984375, 0.0073...
3       [-0.002685546875, -0.01162997159090909, -0.001...
4       [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
                              ...                        
2507    [-0.008582481971153846, -0.01220703125, 0.0178...
2508    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
2509    [-0.002406529017857143, -0.0031912667410714285...
2510    [-0.0039306640625, -0.0111328125, 0.0143310546...
2511    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
Name: result_pretrained, Length: 2512, dtype: object

In [54]:
!pip install KMeans

  Created wheel for KMeans: filename=kmeans-1.0.2-cp39-cp39-macosx_10_9_x86_64.whl size=8510 sha256=a7c764af6f376e54700a516c001f2e30aa2ee8effb51f939b8d03d0507aa047c
  Stored in directory: /Users/ys/Library/Caches/pip/wheels/69/a7/de/4ca4b6cf9a2fd01b7e6e0191e5221227b9600605c25d012126
Successfully built KMeans


In [61]:
from sklearn.cluster import KMeans as km

inertia = []    # cluster 응집도
for k in range(1,31):    # 10개까지
    model = km(k)
    model.fit(result_pretrained)
    inertia.append(model.inertia_)
print(inertia)

[194.22411183710474, 140.86214493369823, 119.40102640667321, 100.83612202280219, 86.23910594906266, 78.39377986967877, 72.45072909184694, 68.53798960472392, 64.80584388847299, 61.53065358581334, 59.03603533431854, 56.94849233113009, 54.47624673761287, 52.39229674588683, 51.1311286106783, 50.52658795229556, 48.420862261468024, 47.739137011911986, 46.66348757549881, 45.71136899902563, 45.15408263351701, 44.6317746541588, 43.53730904968066, 43.236174509840666, 42.381234069297605, 41.88228673624335, 40.6930700566264, 40.33717531993904, 39.759539227037955, 39.39294560886652]


In [64]:
def unsupervised_learning(data, n=28):
    # cluster 개수 -> km_model.inertia_ 를 보면 기울기 변화가 적어지는 부분이 3
    km_model = km(n_clusters = n, algorithm = 'auto')
    km_model.fit(data)    # 학습
    predict_list = km_model.predict(data)    # clustering
    group_list = [[] for _ in range(n)]    # 잘 됐는지 확인하려는 list
    for i in range(n):
        group_list[i] = [ news_df['Title'][idx] for idx,j in enumerate(predict_list) if j == i]
        # init_data는 ['이건 하나의 글입니다', '이건 다른 글이죠', ...] 같은 초기 data
        # print(i, 'group is', group_list[i][:10])     # 각 cluster 당 10개씩 출력
    return predict_list, group_list

In [66]:
predict, group = unsupervised_learning(result_pretrained)

In [76]:
group[20]

['LGU+ "친환경 데이터센터로 소나무 289만 그루 심은 효과"',
 '"데이터 무제한이 제일 나아!” 요즘 AI에이전트, 이 수준이라고? [PLAY IT]',
 '[알림] 데이터로 본 엔데믹 이후의 경영 환경과 CEO의 요건',
 '[BBS경제토크] 나영돈 원장, "구인.구직 인공지능(AI)이 추천"..."데이터 기반 서비스로 전환"',
 '06/15. 암치료에서 인공지능와 빅데이터',
 '[단독]늙어가는 기업연구소…2030 비중 절반으로 추락',
 '[알림] 데이터로 본 엔데믹 이후의 경영 환경과 CEO의 요건',
 '[BBS경제토크] 나영돈 원장, "구인.구직 인공지능(AI)이 추천"..."데이터 기반 서비스로 전환"',
 '06/15. 암치료에서 인공지능와 빅데이터',
 "'전기먹는 하마' 데이터센터, ESG 모범사례로 변신 중",
 "방심위, TBS '김어준의 뉴스공장'에 법정제재 '주의' 의결",
 '[단독]늙어가는 기업연구소…2030 비중 절반으로 추락',
 'TBS 김어준의 뉴스공장에 법정제재…정경심 문서위조 관련',
 'SK가 창출한 ESG 가치 ‘18조원’…“환경 성과는 감소세”',
 'SK가 창출한 ESG 가치 ‘18조원’…“환경 성과는 감소세”',
 '시대가 변한다, 대학이 바뀐다',
 '시대가 변한다, 대학이 바뀐다',
 '[내일날씨] 대구 낮 최고 33도…여름이 성큼',
 '"넌 말 많은 아이야"...나보다 나를 더 잘 아는 너, 도대체 누구니?',
 '‘나의 해방일지’ 손석구 “최고였다! 애정합니다”',
 "전 세계 강제 이주민 '사상 처음' 1억명 돌파",
 "김어준의 뉴스공장 '정경심 보도' 관련 법정제재…KBS도 광고로 '주의'",
 '라이엇, “TFT 용의 땅 세트로 새로운 즐거움 즐길 수 있을 것”',
 "[ET라씨로] LG이노텍, 아이폰14 '전면카메라' 공급 전망에 5%↑",
 '[오늘의 농정 뉴스] 농촌진흥청',
 'SK의 환경성과 고백 “아직은 문제 유발자”',
 "'나의 해방일지', 시청률 6% 자체 최고 경신…

In [49]:
# from tensorflow.keras.preprocessing.text import Tokenizer
# from tensorflow.keras.preprocessing.sequence import pad_sequences

# def text2sequence(df, max_len=100):
#     tokenizer = Tokenizer()
#     tokenizer.fit_on_texts(df)
#     df_seq = tokenizer.texts_to_sequences(df)
#     vocab_size = len(tokenizer.word_index) + 1
#     print('vocab_size : ', vocab_size)
#     seqLi = []
    
# #     for text in df_seq:
# #         seqLi.append(pad_sequences(text, maxlen=max_len))
#     df = pad_sequences(df_seq, maxlen = max_len)
#     return df_seq, vocab_size, tokenizer

# news_df['seq'], vocab_size, tokenizer = text2sequence(news_df['token'])

vocab_size :  2203


In [51]:
# from gensim.models import Word2Vec as w2v

# model = w2v(news_df['token'], window=2, min_count=50, sg=1)

In [52]:
# model.wv.vectors.shape

(9, 100)

In [67]:
# news_df['token'][0]

['kt', 'sat', '스페이스', '데이터', '사업', '진출', '본격', '화']